In [1]:
from dbfread import DBF
import datetime
import struct
from dbfread.struct_parser import StructParser
from dbfread.field_parser import FieldParser

In [3]:

DBFHeader = StructParser(
    'DBFHeader',
    '<BBBBLHHHBBLLLBBH',
    ['dbversion',
     'year',
     'month',
     'day',
     'numrecords',
     'headerlen',
     'recordlen',
     'reserved1',
     'incomplete_transaction',
     'encryption_flag',
     'free_record_thread',
     'reserved2',
     'reserved3',
     'mdx_flag',
     'language_driver',
     'reserved4',
     ])

In [4]:
DBFField = StructParser(
    'DBFField',
    '<11scLBBHBBBB7sB',
    ['name',
     'type',
     'address',
     'length',
     'decimal_count',
     'reserved1',
     'workarea_id',
     'reserved2',
     'reserved3',
     'set_fields_flag',
     'reserved4',
     'index_field_flag',
     ])


In [5]:
print(DBFField.size)


32


In [6]:
TRASPASOS = 'Bases 2022/31-12-2022/Spm2003/2022/traspasos.DBF'


In [7]:
ENCODING = 'cp1252'

In [10]:
def decode_text(data):
    return data.decode(ENCODING)

In [11]:
fields = []
fields_names = []

In [12]:
def read_headers(infile):
    while True:
        sep = infile.read(1)
        if sep in (b'\r', b'\n', b''):
            break
        field = DBFField.unpack(sep + infile.read(DBFField.size - 1))
        field.type = chr(ord(field.type))

        
        if field.type in 'C':
                field.length |= field.decimal_count << 8
                field.decimal_count = 0
        field.name = decode_text(field.name.split(b'\0')[0])
        # print(field.name)
        # if self.lowernames:
        field.name = field.name.lower()

        # self.field_names.append(field.name)
        fields_names.append(field.name)
        fields.append(field)
        # self.fields.append(field)

In [13]:
with open(TRASPASOS, mode='rb') as infile:
    header = DBFHeader.read(infile)
    read_headers(infile)
    # print(header)

In [36]:
print(fields_names)
print(fields)

['nrotrasp', 'orden', 'dccosto', 'accosto', 'cant_pr', 'fechora', 'estado', 'usuario', 'obs_trp', '\r', '', '', '', '', '', '', '', '', '0     ¿‡%', '  ', '    ¿‡%', '', '  ¿‡%', '', '¿‡%', '   549336  ', '%', ' 549337    ', '×xw\x02       ', '49338      ', 'z\x02         ', '339        ', '          j', '0        12', '        jjp', '       127 ', '      jjper', '     610  6', '    jjperez', '   110  112', '  tejido110', ' 611  670  ', 'jjperez   ', '10  611    ', 'perez   ', '  670     ¿', 'rez   ', '112     ¿‡%', '110 ', '0     ¿‡%', '0 ', '    ¿‡%', '', '  ¿‡%', '', '¿‡%', '   549352  ', '%', ' 549353    ', 'ðök\x02       ', '49354      ', 'v\x02         ', '355        ', '          j', '6        61', '        jjp', '       610 ', '      jjper', '     610  6', '    jjperez', '   610  611', '  jjperez  ', ' 670  680  ', 'jjperez   ', '80  140    ', 'perez   ', '  550     ¿', 'rez   ', '600     ¿‡%', 'z   ', '2     ¿‡%', '0 ', '    ¿‡%', '', '  ¿‡%', '', '¿‡%', '   549368  ', '%', ' 

In [21]:
def parseT(data):
        """Parse time field (T)

        Returns datetime.datetime or None"""
        # Julian day (32-bit little endian)
        # Milliseconds since midnight (32-bit little endian)
        #
        # "The Julian day or Julian day number (JDN) is the number of days
        # that have elapsed since 12 noon Greenwich Mean Time (UT or TT) on
        # Monday, January 1, 4713 BC in the proleptic Julian calendar
        # 1. That day is counted as Julian day zero. The Julian day system
        # was intended to provide astronomers with a single system of dates
        # that could be used when working with different calendars and to
        # unify different historical chronologies." - wikipedia.org

        # Offset from julian days (used in the file) to proleptic Gregorian
        # ordinals (used by the datetime module)
        offset = 1721425  # Todo: will this work?

        if data.strip():
            # Note: if the day number is 0, we return None
            # I've seen data where the day number is 0 and
            # msec is 2 or 4. I think we can safely return None for those.
            # (At least I hope so.)
            #
            day, msec = struct.unpack('<LL', data)
            if day:
                dt = datetime.datetime.fromordinal(day - offset)
                delta = datetime.timedelta(seconds=msec/1000)
                return dt + delta
            else:
                return None
        else:
            return None

In [43]:
def get_record(file_name, index):
    with open(file_name, mode='rb') as infile:
        infile.seek(header.headerlen + index * header.recordlen)
        read = infile.read
        read(1)
        currentItems = []
        for field in fields:
            # print(field.name, field.type, field.length)
            data = read(field.length)
            if field.type == 'N':
                data = decode_text(data)
                try:
                    data = int(data)
                except ValueError:
                    data = None
            if field.type in 'T':
                # print('T')
                data = parseT(data)
            if field.type in 'C':
                # print('C')
                data = decode_text(data.rstrip())
            elif field.type == 'D':
                # print('D')
                data = decode_text(data)
                try:
                    data = datetime.date(int(data[:4]), int(data[4:6]), int(data[6:8]))
                except ValueError:
                    data = None
            elif field.type in 'FI':
                # print('FI')
                data = decode_text(data)
                try:
                    data = int(data)
                except ValueError:
                    data = None
            elif field.type == 'NL':
                # print('NL')
                data = decode_text(data)
                try:
                    data = float(data)
                except ValueError:
                    data = None
            currentItems.append((field.name, data))
        return dict(currentItems)
            
        # record = infile.read(header.recordlen)

           
        #  return dict(currentItems)

        #   infile.seek(header.headerlen + index * header.recordlen)
        #   record = infile.read(header.recordlen)
        #   return record

In [44]:
rec = get_record(TRASPASOS, 0)
print(rec)

{'nrotrasp': 549332, 'orden': '', 'dccosto': '670', 'accosto': '680', 'cant_pr': None, 'fechora': datetime.datetime(2022, 1, 3, 10, 30, 49), 'estado': '', 'usuario': 'JJPEREZ', 'obs_trp': b'\x00\x00\x00\x00'}


In [ ]:
"""
    [ ] porque el header es 587 bytes
    [ ] cada registro es 62 bytes
    [ ] leer dbf en wikipedia
    [ ] saber la cantidad de registros que tiene el archivo
"""

In [125]:
#52 bytes por registro
with open(TRASPASOS, 'rb') as f:
    f.seek(587+27)
    # f.seek(52*3)
    NROTRASP = f.read(8)
    NROTRASPText = NROTRASP.decode('cp1252')
    parseDate = parseT(NROTRASP)
    print(NROTRASP)
    print(NROTRASPText)
    print(parseDate)
    

b'\xbf\x87%\x00\xa8\x87A\x02'
¿‡% ¨‡A
2022-01-03 10:30:49


In [98]:
with open(TRASPASOS, 'rb') as archivo_dbf:
    # archivo_dbf.seek(0, 2)
    archivo_dbf.seek(587)
    NROTRASP = archivo_dbf.read(8)
    ORDEN = archivo_dbf.read(6)
    DCCOSTO = archivo_dbf.read(5)
    ACCOSTO = archivo_dbf.read(5)
    CANT_PR = archivo_dbf.read(3)
    FEC_HORA = archivo_dbf.read(8)
    ESTADO = archivo_dbf.read(10)
    USUARIO = archivo_dbf.read(10)
    OBS_TRP = archivo_dbf.read(7)
    NROTRASPText = NROTRASP.decode('cp1252')
    ORDENText = ORDEN.decode('cp1252')
    DCCOSTOText = DCCOSTO.decode('cp1252')
    ACCOSTOText = ACCOSTO.decode('cp1252')
    CANT_PRText = CANT_PR.decode('cp1252')
    #convert to time format
    # FEC_HORAText = FEC_HORA.decode('cp1252')
    FEC_HORAText = FEC_HORA.decode('cp1252')  # Decodifica los bytes a una cadena
    ESTADOText = ESTADO.decode('cp1252')
    USUARIOText = USUARIO.decode('cp1252')
    OBS_TRPText = OBS_TRP.decode('cp1252')

    NEXTNRTRASP = archivo_dbf.read(8)
    NEXTNRTRASP_Text = NEXTNRTRASP.decode('cp1252')
    
    print(NROTRASPText)
    print(ORDENText)
    print(DCCOSTOText)
    print(ACCOSTOText)
    print(CANT_PRText)
    # print(FEC_HORAText)
    print(ESTADOText)
    print(USUARIOText)
    print(OBS_TRPText)

    print(NEXTNRTRASP_Text)
    

La fecha no está en el formato esperado.
549332  
      
670  
680  
   
          
JJPEREZ   
       
549333  


In [33]:
# Abre el archivo DBF en modo binario ('rb')
with open(TRASPASOS, 'rb') as archivo_dbf:
    # Lee el encabezado del archivo DBF
    encabezado = archivo_dbf.read(64)  # El encabezado tiene 32 bytes

    # Obtiene el número de registros (en little-endian)
    num_registros = int.from_bytes(encabezado[4:8], 'little')

    # Calcula la longitud de los registros (en little-endian)
    longitud_registro = int.from_bytes(encabezado[8:10], 'little')

    # Define la estructura de campos (nombre, tipo, longitud)
    estructura_campos = [
        ('NROTRASP', 'N', 8),
        ('ORDEN', 'C', 8),
        ('DCCOSTO', 'C', 5),
        ('ACCOSTO', 'C', 5),
        ('CANT_PR', 'N', 3),
        ('FECHORA', 'T', 8),
        ('ESTADO', 'C', 10),
        ('USUARIO', 'C', 10),
        ('OBS_TRP', 'M', 4)
    ]

    # Itera a través de los registros
    for _ in range(num_registros):
        registro = archivo_dbf.read(longitud_registro)
        datos = {}
        offset = 1  # El offset inicial es 1, ya que el primer byte es un marcador de eliminación
        for nombre, tipo, longitud in estructura_campos:
            try:
                valor = registro[offset:offset + longitud].decode('utf-8').strip()
            except UnicodeDecodeError:
                # Intenta con otra codificación (por ejemplo, Latin-1)
                valor = registro[offset:offset + longitud].decode('latin-1').strip()
            datos[nombre] = valor
            offset += longitud
        print(datos)


{'NROTRASP': 'RDEN\x00\x00\x00\x00', 'ORDEN': '\x00\x00C\t\x00\x00\x00\x08', 'DCCOSTO': '\x00\x00\x00\x00\x00', 'ACCOSTO': '\x00\x00\x00\x00\x00', 'CANT_PR': '\x00\x00\x00', 'FECHORA': '\x00\x00DCCOST', 'ESTADO': 'O\x00\x00\x00\x00C\x11\x00\x00\x00', 'USUARIO': '\x05\x00\x00\x00\x00\x00\x00\x00\x00\x00', 'OBS_TRP': '\x00\x00\x00\x00'}
{'NROTRASP': '549333', 'ORDEN': '61', 'DCCOSTO': '1  67', 'ACCOSTO': '0', 'CANT_PR': '¿\x87', 'FECHORA': '%\x00×=L\x02', 'ESTADO': 'JJ', 'USUARIO': 'PEREZ   \x00\x00', 'OBS_TRP': '\x00\x00'}
{'NROTRASP': '¿\x87%\x00È-]', 'ORDEN': '\x02', 'DCCOSTO': 'JJ', 'ACCOSTO': 'PEREZ', 'CANT_PR': '', 'FECHORA': '\x00\x00\x00\x00   5', 'ESTADO': '49343', 'USUARIO': '110  11', 'OBS_TRP': '2'}
{'NROTRASP': '\x00\x00\x00\x00', 'ORDEN': '549352', 'DCCOSTO': '', 'ACCOSTO': '67', 'CANT_PR': '0', 'FECHORA': '680', 'ESTADO': "¿\x87%\x00ç'k\x02", 'USUARIO': 'JJ', 'OBS_TRP': 'PERE'}
{'NROTRASP': '0  140', 'ORDEN': '¿\x87%\x00\x9f', 'DCCOSTO': '\x02\x88\x02', 'ACCOSTO': '', 'CAN